In [1]:
import torch 
from torch import nn
from torch.utils.data import random_split
import numpy as np
import torch.optim as optim
torch.manual_seed(42)

In [2]:
def generate_sample(low = 2, high = 10):
    """
        Generates a sample of random length between 'low' and 'high', with random values b/w [0, 1] in the 1st dimension
        and with two 1s in the 2nd dimension. 
        The label = sum of the random values whose 2nd dimensions are marked by 1.
    
    Returns :
        x: A 2D array of random length b/w 'low' and 'high'
        y: The sum of the random values whose 2nd dimensions are marked by 1
                                                                                                                    """
    # n = length of sequence b/w 2 and 10 by default
    n = np.random.randint(low, high)
    
    # x is a 2D vector , 1st dimension contains values b/w 0 and 1 , 2nd dimension alll 0s
    x = np.random.rand(n, 2)
    x[:, 1] = 0
    
    # Choose any 2 indices randomly and make x[indices, 1] = 1
    rand_indices = np.random.choice(n, 2, replace=False)
    x[rand_indices, 1] = 1
    
    y = x[:, 0] * x[:, 1]
    return x, y.sum()


In [3]:
#################################################### Elman network ##########################################################                

class ElmanNet(nn.Module):
    def __init__(self, input_size, hidden_size, op_size):
        super().__init__()
        self.input_size = input_size
        self.hidden_size = hidden_size
        self.op_size = op_size
        
         
        # Initialise the weight (Xavier initialisation) 
        self.W_xh = torch.rand((hidden_size, input_size), requires_grad=True)  # 3 x 2  
        self.W_hh = torch.rand((hidden_size, hidden_size), requires_grad=True) # 3 x 3
        self.W_hy = torch.rand((op_size, hidden_size), requires_grad=True)  # 1 x 3
#         nn.init.xavier_uniform_(self.W_xh)
#         nn.init.xavier_uniform_(self.W_hh)
#         nn.init.xavier_uniform_(self.W_hy)
        
        self.b_h = torch.rand(hidden_size, requires_grad=True)               # 3 x 1
        self.b_y = torch.rand(op_size, requires_grad=True)                # 1 x 1
        
        
        # Hidden state is initialised as zero
        self.h_t = torch.zeros(hidden_size)
    
    def forward(self, x):
        """ 
        x : numpy 2D array : 1st dimension b/w [0,1] and 2nd dimension having 1 in 2 places
        Returns:
            y : scalar value : predicted value.
                                                                                                """        
        H = self.h_t
        for t in range(x.shape[0]):
#             H = torch.tanh(torch.matmul(self.W_xh ,torch.Tensor(x[t]).unsqueeze(1)) + torch.matmul(self.W_hh, H) + self.b_h)
            H = torch.tanh(self.W_xh @ torch.Tensor(x[t]) + self.W_hh @ H + self.b_h)
            

        y = self.W_hy@ H + self.b_y
        
        
        return y
    
    
    def train(self, net, datas, n_epochs = 20):
        """ 
            Trains the network {net} for {n_epochs} epochs using the train data {datas} 
            net : A instantiated neural network class
            datas : Train data is a list of tuples where tuples are of the form ({2D array of variable length}, {label})
            n_epochs : Number of epochs to train for.
                                                                                                                        """
        # Define the optimiser and loss function
        optimizer = optim.SGD([self.W_xh, self.W_hh, self.W_hy, self.b_h, self.b_y], lr=0.05)
        criterion = nn.MSELoss()                         # (Loss fn = MSE)
        
        # Training loop
        for epoch in range(n_epochs):
            cumulative_loss = 0
            for i, data in enumerate(datas, 0):
                
                # Get inputs and labels
                inputs, labels = data

                # Forward + backward prop using the loss defined + optimize using the optimiser defined 
                y_pred = self.forward(inputs)
                
                # Zero the parameter gradients
                optimizer.zero_grad()
                
#                 print(y_pred)
#                 print(torch.tensor([labels]).unsqueeze(1).float())
                loss = criterion(y_pred, torch.tensor([labels]).float())
                print(loss)
                print(y_pred, torch.tensor([labels]).float())
#               loss = (y_pred - torch.tensor([labels])) * (y_pred - torch.tensor([labels]))
                
#                 print(loss)
                # Compute gradients using backward pass
                loss.backward()
#                 print(self.W_xh.grad)
                # Update the parameters using the gradients and Adam optimiser
                optimizer.step()

                # Update running loss
                cumulative_loss += loss.detach()

            
            cumulative_loss = cumulative_loss/len(datas)
            print(f"Epoch {epoch}, Epoch_loss {cumulative_loss}. ")
                

#################################################### LSTM network ##########################################################                
                
class LSTMnet(nn.Module):
    def __init__(self, ip_size, h_size, op_size):
        super().__init__()
        self.ip_size = ip_size
        self.h_size = h_size
        self.op_size = op_size
        
        # (Xavier weigth initialisation) 
         # I/p gate , Hidden state , forget gate, o/p gate weights
        self.W_ch = nn.Parameter(torch.empty(h_size, h_size), requires_grad=True) 
        self.W_cx = nn.Parameter(torch.empty(h_size, ip_size), requires_grad=True) 
        self.W_fh = nn.Parameter(torch.empty(h_size, h_size), requires_grad=True) 
        self.W_fx = nn.Parameter(torch.empty(h_size, ip_size), requires_grad=True) 
        self.W_ih = nn.Parameter(torch.empty(h_size, h_size), requires_grad=True) 
        self.W_ix = nn.Parameter(torch.empty(h_size, ip_size), requires_grad=True) 
        self.W_oh = nn.Parameter(torch.empty(h_size, h_size), requires_grad=True) 
        self.W_ox = nn.Parameter(torch.empty(h_size, ip_size), requires_grad=True)
        nn.init.xavier_uniform_(self.W_ch)
        nn.init.xavier_uniform_(self.W_cx)
        nn.init.xavier_uniform_(self.W_fh)
        nn.init.xavier_uniform_(self.W_fx)
        nn.init.xavier_uniform_(self.W_ih)
        nn.init.xavier_uniform_(self.W_ix)
        nn.init.xavier_uniform_(self.W_oh)
        nn.init.xavier_uniform_(self.W_ox)
        
        # I/p gate , Hidden state , forget gate, o/p gate biases
        self.b_c = nn.Parameter(torch.zeros(h_size, 1), requires_grad=True)               
        self.b_f = nn.Parameter(torch.zeros(h_size, 1), requires_grad=True)               
        self.b_i = nn.Parameter(torch.zeros(h_size, 1), requires_grad=True)               
        self.b_o = nn.Parameter(torch.zeros(h_size, 1), requires_grad=True)               

        # Output layer weights and biases
        self.W_hy = nn.Parameter(torch.empty(op_size, h_size), requires_grad=True)  
        nn.init.xavier_uniform_(self.W_hy)        
        self.b_y = nn.Parameter(torch.zeros(op_size, 1), requires_grad=True)                
        
        # hidden state and cell states are initialised as zero vectors
        self.h_t = torch.zeros(h_size, 1)
        self.c_t = torch.zeros(h_size, 1)
    
    def forward(self, x):
        """ 
        x : numpy 2D array : 1st dimension b/w [0,1] and 2nd dimension having 1 in 2 places
        Returns:
            y : scalar value : predicted value.
        """        
        H = self.h_t
        C_t = self.c_t
        
        for t in range(x.shape[0]):
            I_t = torch.sigmoid(torch.matmul(self.W_ix.data ,torch.Tensor(x[t]).unsqueeze(1)) + torch.matmul(self.W_ih.data, H) + self.b_i)
            F_t = torch.sigmoid(torch.matmul(self.W_fx.data ,torch.Tensor(x[t]).unsqueeze(1)) + torch.matmul(self.W_fh.data, H) + self.b_f)
            O_t = torch.sigmoid(torch.matmul(self.W_ox.data ,torch.Tensor(x[t]).unsqueeze(1)) + torch.matmul(self.W_oh.data, H) + self.b_o)
            Ct_hat = torch.tanh(torch.matmul(self.W_cx.data ,torch.Tensor(x[t]).unsqueeze(1)) + torch.matmul(self.W_ch.data, H) + self.b_c)
            
            C_t = torch.mul(F_t, C_t) + torch.mul(I_t, Ct_hat)
            H = torch.mul(O_t, torch.tanh(C_t))
            
        y = torch.relu(torch.matmul(self.W_hy.data, H) + self.b_y)
        
        return y
    
    def train(self, net, datas, n_epochs = 20):
        """ 
            Trains the network {net} for {n_epochs} epochs using the train data {datas} 
            net : A instantiated neural network class
            datas : Train data is a list of tuples where tuples are of the form ({2D array of variable length}, {label})
            n_epochs : Number of epochs to train for.
                                                                                                                        """
        # Define the optimiser and loss function
        optimizer = optim.SGD(net.parameters(), lr=0.05)
        criterion = nn.MSELoss()                         # (Loss fn = MSE)
        
        # Training loop
        for epoch in range(n_epochs):
            cumulative_loss = 0
            for i, data in enumerate(datas, 0):
                
                # Get inputs and labels
                inputs, labels = data
                
                # Zero the parameter gradients
                optimizer.zero_grad()

                # Forward + backward prop using the loss defined + optimize using the optimiser defined 
                y_pred = self.forward(inputs)
                loss = criterion(y_pred, torch.tensor([labels]).unsqueeze(1).float())
                
                # Compute gradients using backward pass
                loss.backward()
                
        
                # Update the parameters using the gradients and Adam optimiser
                optimizer.step()

                # Update running loss
                cumulative_loss += loss.detach()

            
            cumulative_loss = cumulative_loss/len(datas)
            print(f"Epoch {epoch}, Epoch_loss {cumulative_loss}. ")

            

In [ ]:
# Define hyperparameters
input_size = 2
output_size = 1
n_epochs = 20
hidden_sizes = [20]

# n_samples to generate
n_samples = 8000
datas = [generate_sample() for _ in range(n_samples)]      # data is a LIST


# Split dataset into train and validation sets 
train_size = int(0.8 * len(datas))
val_size = len(datas) - train_size
train_datas, val_datas = random_split(datas, [train_size, val_size]) 


for hidden_size in hidden_sizes:
    # Instantiate model and optimizer
    net = ElmanNet(input_size, hidden_size, output_size)
    net.train(net, train_datas, n_epochs)
    

# Prediction
print(val_datas[0])
print(val_datas[0][0])
net.forward(val_datas[0][0])



tensor([8.6909], grad_fn=<AddBackward0>) tensor([0.5359])
tensor([-8.4346], grad_fn=<AddBackward0>) tensor([0.5737])
tensor([10.4828], grad_fn=<AddBackward0>) tensor([1.6382])
tensor([-8.0908], grad_fn=<AddBackward0>) tensor([0.7868])
tensor([10.5523], grad_fn=<AddBackward0>) tensor([1.0826])
tensor([-9.3340], grad_fn=<AddBackward0>) tensor([0.9608])
tensor([12.2852], grad_fn=<AddBackward0>) tensor([0.9311])
tensor([-11.5584], grad_fn=<AddBackward0>) tensor([1.1598])
tensor([15.1499], grad_fn=<AddBackward0>) tensor([1.1263])
tensor([-14.2997], grad_fn=<AddBackward0>) tensor([0.8010])
tensor([17.4118], grad_fn=<AddBackward0>) tensor([0.5045])
tensor([-18.0936], grad_fn=<AddBackward0>) tensor([1.3497])
tensor([22.7372], grad_fn=<AddBackward0>) tensor([0.9762])
tensor([-22.9610], grad_fn=<AddBackward0>) tensor([0.8714])
tensor([27.0871], grad_fn=<AddBackward0>) tensor([0.8256])
tensor([-28.0620], grad_fn=<AddBackward0>) tensor([1.0454])
tensor([33.0636], grad_fn=<AddBackward0>) tensor([1.

tensor([105055.7969], grad_fn=<AddBackward0>) tensor([0.4517])
tensor([-115560.4297], grad_fn=<AddBackward0>) tensor([0.9346])
tensor([127118.4453], grad_fn=<AddBackward0>) tensor([0.2566])
tensor([-137177.6562], grad_fn=<AddBackward0>) tensor([1.1215])
tensor([150897.7656], grad_fn=<AddBackward0>) tensor([0.9724])
tensor([-165893.9844], grad_fn=<AddBackward0>) tensor([0.3099])
tensor([182484.0312], grad_fn=<AddBackward0>) tensor([0.7214])
tensor([-200730.9375], grad_fn=<AddBackward0>) tensor([0.3481])
tensor([183884.7969], grad_fn=<AddBackward0>) tensor([0.6388])
tensor([-128575.1406], grad_fn=<AddBackward0>) tensor([1.1373])
tensor([141435.0312], grad_fn=<AddBackward0>) tensor([1.3958])
tensor([-155575.5938], grad_fn=<AddBackward0>) tensor([0.6231])
tensor([171134.4375], grad_fn=<AddBackward0>) tensor([1.2492])
tensor([-256259.1562], grad_fn=<AddBackward0>) tensor([1.7391])
tensor([281888.7188], grad_fn=<AddBackward0>) tensor([1.0414])
tensor([-236936.1562], grad_fn=<AddBackward0>) t

tensor([28359326.], grad_fn=<AddBackward0>) tensor([1.0310])
tensor([-36995560.], grad_fn=<AddBackward0>) tensor([0.5709])
tensor([40695116.], grad_fn=<AddBackward0>) tensor([0.7911])
tensor([-42546700.], grad_fn=<AddBackward0>) tensor([1.4027])
tensor([36074096.], grad_fn=<AddBackward0>) tensor([1.1527])
tensor([-39681508.], grad_fn=<AddBackward0>) tensor([0.9190])
tensor([40959056.], grad_fn=<AddBackward0>) tensor([1.2034])
tensor([-34172552.], grad_fn=<AddBackward0>) tensor([0.8683])
tensor([37589812.], grad_fn=<AddBackward0>) tensor([0.9811])
tensor([-41348796.], grad_fn=<AddBackward0>) tensor([0.4808])
tensor([45483680.], grad_fn=<AddBackward0>) tensor([1.1263])
tensor([-50032048.], grad_fn=<AddBackward0>) tensor([0.4052])
tensor([55035256.], grad_fn=<AddBackward0>) tensor([1.1427])
tensor([-60538780.], grad_fn=<AddBackward0>) tensor([1.1081])
tensor([66592660.], grad_fn=<AddBackward0>) tensor([1.1523])
tensor([-73251920.], grad_fn=<AddBackward0>) tensor([1.5775])
tensor([80577104

tensor([-1.6509e+12], grad_fn=<AddBackward0>) tensor([1.5673])
tensor([1.8160e+12], grad_fn=<AddBackward0>) tensor([1.4680])
tensor([-1.9976e+12], grad_fn=<AddBackward0>) tensor([1.7066])
tensor([2.1973e+12], grad_fn=<AddBackward0>) tensor([1.6053])
tensor([-2.4170e+12], grad_fn=<AddBackward0>) tensor([0.8540])
tensor([2.6587e+12], grad_fn=<AddBackward0>) tensor([1.0343])
tensor([-2.9246e+12], grad_fn=<AddBackward0>) tensor([0.5995])
tensor([3.2171e+12], grad_fn=<AddBackward0>) tensor([1.6384])
tensor([-3.5388e+12], grad_fn=<AddBackward0>) tensor([0.8074])
tensor([3.8927e+12], grad_fn=<AddBackward0>) tensor([1.0978])
tensor([-4.2819e+12], grad_fn=<AddBackward0>) tensor([0.9732])
tensor([4.7101e+12], grad_fn=<AddBackward0>) tensor([0.4958])
tensor([-5.1811e+12], grad_fn=<AddBackward0>) tensor([1.1769])
tensor([5.6993e+12], grad_fn=<AddBackward0>) tensor([0.8721])
tensor([-6.2692e+12], grad_fn=<AddBackward0>) tensor([1.3023])
tensor([6.8961e+12], grad_fn=<AddBackward0>) tensor([1.3274])


tensor([1.4829e+17], grad_fn=<AddBackward0>) tensor([0.9280])
tensor([-1.6311e+17], grad_fn=<AddBackward0>) tensor([1.3196])
tensor([1.7943e+17], grad_fn=<AddBackward0>) tensor([1.4580])
tensor([-2.2048e+17], grad_fn=<AddBackward0>) tensor([1.7982])
tensor([2.2154e+17], grad_fn=<AddBackward0>) tensor([0.6111])
tensor([-2.4369e+17], grad_fn=<AddBackward0>) tensor([1.7946])
tensor([2.8462e+17], grad_fn=<AddBackward0>) tensor([0.7774])
tensor([-2.7271e+17], grad_fn=<AddBackward0>) tensor([0.9672])
tensor([2.9998e+17], grad_fn=<AddBackward0>) tensor([1.4457])
tensor([-3.2998e+17], grad_fn=<AddBackward0>) tensor([0.4371])
tensor([2.6207e+17], grad_fn=<AddBackward0>) tensor([1.2248])
tensor([-1.3495e+17], grad_fn=<AddBackward0>) tensor([1.1521])
tensor([1.4845e+17], grad_fn=<AddBackward0>) tensor([0.9888])
tensor([-3.1392e+17], grad_fn=<AddBackward0>) tensor([1.3414])
tensor([4.3315e+17], grad_fn=<AddBackward0>) tensor([1.9339])
tensor([-4.7646e+17], grad_fn=<AddBackward0>) tensor([0.7785])


...

tensor([nan], grad_fn=<AddBackward0>) tensor([0.8762])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9084])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1652])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7093])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.3692])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.6339])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3958])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4267])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3011])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.9409])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.6487])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1831])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.6175])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.2223])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9324])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9077])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9690])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4348])
tensor([na

tensor([nan], grad_fn=<AddBackward0>) tensor([0.4804])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4087])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7085])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.5732])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7358])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4222])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4912])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.7835])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.8015])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0554])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0163])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.1934])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9041])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4621])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.2463])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8638])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7697])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0684])
tensor([na

tensor([nan], grad_fn=<AddBackward0>) tensor([1.5554])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1503])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4968])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7243])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3023])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8173])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9076])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.5763])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.2776])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0388])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8890])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3036])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1878])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1520])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.5965])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3105])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7429])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4446])
tensor([na

tensor([nan], grad_fn=<AddBackward0>) tensor([1.3934])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3410])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.7643])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.2563])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9961])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9621])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0982])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9897])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4476])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8279])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9861])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.3654])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.6662])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1694])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.1408])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4017])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8880])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0690])
tensor([na

tensor([nan], grad_fn=<AddBackward0>) tensor([1.0901])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.2723])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0259])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7064])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.1440])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4198])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.8371])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0720])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.5861])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.5467])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.9685])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.8956])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.6305])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.4701])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.4099])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.7374])
tensor([nan], grad_fn=<AddBackward0>) tensor([0.7721])
tensor([nan], grad_fn=<AddBackward0>) tensor([1.0793])
tensor([na

In [ ]:
# Define hyperparameters and generate dataset fro LSTM net
input_size = 2
output_size = 1
n_epochs = 20
hidden_sizes = [10]

# n_samples to generate
n_samples = 8000
datas = [generate_sample() for _ in range(n_samples)]

# Split dataset into train and validation sets 
train_size = int(0.8 * len(datas))
val_size = len(datas) - train_size
train_datas, val_datas = random_split(datas, [train_size, val_size]) 


for hidden_size in hidden_sizes:
    # Instantiate model and optimizer
    LSTMnet = LSTMnet(input_size, hidden_size, output_size)
    LSTMnet.train(LSTMnet, train_datas, n_epochs)
    

# Prediction
print(val_datas[0])
print(val_datas[0][0])
LSTMnet.forward(val_datas[0][0])